# Initiez-vous au MLOps (partie 1/2)
## Option B - Exercice - Élaborez un modèle de scoring

Vous êtes Data Scientist au sein d'une société financière, nommée "Prêt à dépenser", qui propose des crédits à la consommation pour des personnes ayant peu ou pas du tout d'historique de prêt.
 
L’entreprise souhaite mettre en œuvre un outil de “scoring crédit” pour calculer la probabilité qu’un client rembourse son crédit, puis classifie la demande en crédit accordé ou refusé. Elle souhaite donc développer un algorithme de classification en s’appuyant sur des sources de données variées (données comportementales, données provenant d'autres institutions financières, etc.)

La mission :
- Construire et optimiser un modèle de scoring qui donnera une prédiction sur la probabilité de faillite d'un client de façon automatique.
- Analyser les features qui contribuent le plus au modèle, d’une manière générale (feature importance globale) et au niveau d’un client (feature importance locale), afin, dans un soucis de transparence, de permettre à un chargé d’études de mieux comprendre le score attribué par le modèle.
- Mettre en œuvre une approche globale MLOps de bout en bout, du tracking des expérimentations à la pré-production du modèle.

Mise en oeuvre des étapes orientées MLOps suivantes :
- Dans le notebook d’entraînement des modèles, générer à l’aide de MLFlow un tracking d'expérimentations.
- Lancer l’interface web “UI MLFlow" d'affichage des résultats du tracking.
- Réaliser avec MLFlow un stockage centralisé des modèles dans un “model registry”.
- Tester le serving MLFlow.

### Objectif de cette étape :
* Mettre en place les fonctions de nettoyage et les appliquées.
* Application également de l'encodage des varibales catégorielles
* Aggrégation des sous-tables puis fusion avec le fichier principal (fusion au préalable de train et test)
* Imputation des valeurs manquantes avec SimpleImputer
* Gestion des fonctions via les scripts dans src car difficelemnt lisibles sinon

* Comme indiqué dans l'énoncé, pour la réalisation de ces éléments, notamment des différentes fonctions à appliquer sur les fichiers, utilisation du kernel suivant :
   * https://www.kaggle.com/code/jsaguiar/lightgbm-with-simple-features/script


## Importation des librairies

In [1]:
# Librairies de base
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Libraires scikit-learn
from sklearn.impute import SimpleImputer

# Visualisation des valeurs manquantes
import missingno as msno

# Meilleure visualisation des grands df
import itables.options as opt
from itables import show

# Activation de l’affichage interactif automatiquement dans les notebooks
opt.warn_on_undocumented_option = False
opt.notebook_connected = True
opt.maxBytes = 0 # Pour ne pas tronquer les gros DataFrames
opt.maxColumns = 0

# Afin de récupérer les dossiers dans src
import sys, os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))

# Importation de toutes les fonctions ajoutées
from src.data_cleaning import cleaning_application_test_train
from src.feature_aggregations import one_hot_encoder
from src.feature_aggregations import process_bureau_and_balance
from src.feature_aggregations import process_previous_applications
from src.feature_aggregations import process_pos_cash
from src.feature_aggregations import process_installments
from src.feature_aggregations import process_credit_card
from src.prepare_application_data import prepare_application_data
from src.build_dataset import build_dataset
from src.impute_numeric_only import impute_numeric_only


##### On commence par importer nos fichiers initiaux

In [2]:
# Chargement des fichiers CSV
app_train = pd.read_csv("../data/raw/application_train.csv")
app_test = pd.read_csv("../data/raw/application_test.csv")
bureau = pd.read_csv("../data/raw/bureau.csv")
bureau_balance = pd.read_csv("../data/raw/bureau_balance.csv")
previous_application = pd.read_csv("../data/raw/previous_application.csv")
cash_balance = pd.read_csv("../data/raw/POS_CASH_balance.csv")
installments_payments = pd.read_csv("../data/raw/installments_payments.csv")
credit_card_balance = pd.read_csv("../data/raw/credit_card_balance.csv")

##### Préparation et nettoyage des deux fichiers principaux : application_train et appplication_test
Concrétement nous avons fait ces 2 fonctions :

* prepare_application_data.py : elle permet de fusionner train et test afin d'y appliquer la fonction data_cleaning.py.
* data_cleaning.py : fichier utilisé dans prepare_application_data.py va réaliser :
    * le nettoyage des formats
    * la gestion des valeurs abérrantes
    * le feature engineering
    * l'encodage des variables catégorielles
* Pour le feature engineering, création des nouvelles données suivantes :

* === Feature engineering de base ===
    * df["DAYS_EMPLOYED_PERC"] = df["DAYS_EMPLOYED"] / df["DAYS_BIRTH"]
    * df["INCOME_CREDIT_PERC"] = df["AMT_INCOME_TOTAL"] / df["AMT_CREDIT"]
    * df["INCOME_PER_PERSON"] = df["AMT_INCOME_TOTAL"] / df["CNT_FAM_MEMBERS"]
    * df["ANNUITY_INCOME_PERC"] = df["AMT_ANNUITY"] / df["AMT_INCOME_TOTAL"]
    * df["PAYMENT_RATE"] = df["AMT_ANNUITY"] / df["AMT_CREDIT"]

In [3]:
full_data = prepare_application_data(app_train, app_test)

=== Préparation du dataset complet (train + test) ===
→ Fusion train/test : (356255, 123)
 Nettoyage terminé → shape : (356251, 256)
→ Nettoyage terminé : (356251, 256)


##### Vérification rapide des changements

In [4]:
show(full_data.head())

#### Sur les sous-tables : application du kernel Kaggle afin de respecter les consignes :
* https://www.kaggle.com/code/jsaguiar/lightgbm-with-simple-features/script
* Ici nous réalisons les aggrégations des fichiers afin d'obtenir des moyennes, sommes etc afin d'éviter les doublons, tout est rattaché au final à la clé SK_ID_CURR
* 2 colonnes avec 99% de valeurs manquantes sont supprimées dans previous_application
* Il y a un OneHot qui est réalisé pour les valeurs catégorielles
* A noter, un ajustement a été réalisé par rapport au kernel sur la gestion des "False" afin de les mettre en binaire


#### Lancement des fonctions des sous-tables via feature_aggregation.py

In [5]:
bureau_agg = process_bureau_and_balance(bureau, bureau_balance)
previous_agg = process_previous_applications(previous_application)
pos_agg = process_pos_cash(cash_balance)
install_agg = process_installments(installments_payments)
credit_agg = process_credit_card(credit_card_balance)

##### Fonction build_dataset.py afin d'obtenir un seul DataFrame (2 en comptant le test)
* Fusion des sous-tables avec train & test
* Vérification pour ne pas avoir de duplication de lignes
* Harmonisation et check pour ne pas avoir de True ou False mais seulement des valeurs numériques ou NaN

In [6]:
app_train_final = build_dataset(full_data,
                  bureau_agg, previous_agg, pos_agg,
                  install_agg, credit_agg)

 Fusion des sous-tables...
    Fusion bureau          | avant: (356251, 256), après: (356251, 345)
    Fusion previous        | avant: (356251, 345), après: (356251, 552)
    Fusion pos_cash        | avant: (356251, 552), après: (356251, 570)
    Fusion installments    | avant: (356251, 570), après: (356251, 581)
    Fusion credit_card     | avant: (356251, 581), après: (356251, 722)

 Fusion terminée avec succès !
   → TRAIN shape : (356251, 722)

 Harmonisation post-fusion...

 Vérification et correction finale des valeurs 'False'...
    679 colonnes corrigées dans TRAIN

 Vérification finale :
   → Colonnes bool restantes TRAIN : 0

 Nettoyage complet — datasets prêts pour imputation et modélisation !


In [7]:
show(app_train_final.head())

#### Application de la technique SimpleImputer avec la médiane pour gérer les valeurs manquantes

In [8]:
app_train_final = impute_numeric_only(app_train_final)

 Début de l’imputation (numérique uniquement)...
 Imputation terminée avec succès
   → TRAIN shape : (356251, 722)


In [9]:
show(app_train_final.head(1000))

#### Enregistrement du DF finalisé

In [10]:
app_train_final.to_csv("../data/processed/app_train_modelisation.csv", index=False)